## This panel wiill provide a bam file viewer

In [184]:
import os, sys, io, random, subprocess
import string
import numpy as np
import pandas as pd
from importlib import reload

from Bio.Seq import Seq
from Bio.SeqRecord import SeqRecord
from Bio.Align import MultipleSeqAlignment
from Bio import AlignIO, SeqIO

from IPython.display import HTML

from bokeh.plotting import figure
from bokeh.models import ColumnDataSource, Plot, LinearAxis, Grid, Range1d,CustomJS, Slider, HoverTool, NumeralTickFormatter, Label
from bokeh.models.glyphs import Text, Rect
from bokeh.layouts import gridplot, column
import panel as pn
import panel.widgets as pnw
pn.extension()

from pybioviz import viewers, plotters, utils

In [271]:
reload(utils)
df = utils.get_bam_aln('SRR650219.sorted.bam', 'RD900MAF', 1500, 1600)
print (df)
p = plot_bam_alignment('SRR650219.sorted.bam','RD900MAF', 1400, 1600,plot_width=500, plot_height=150)
pn.pane.Bokeh(p)
p2 = plot_bam_alignment('SRR650219.sorted.bam','RD900MAF', 1450, 1650,plot_width=500, plot_height=150)
pn.Row(pn.pane.Bokeh(p),pn.pane.Bokeh(p2))

   start   end    cigar              name  length  mapq  y
0   1374  1518     144M  SRR650219.144565     144    60  1
1   1414  1530     116M  SRR650219.144570     116    60  2
2   1445  1514      69M  SRR650219.144575      69    51  3
3   1461  1565  104M41S  SRR650219.478449     145     0  4
4   1461  1563  11S102M  SRR650219.478449     113     0  5
5   1477  1577   100M2S  SRR650219.144578     102     0  6
6   1477  1577  11S100M  SRR650219.144578     111     0  7


Row
    [0] Bokeh(Figure)
    [1] Bokeh(Figure)

In [ ]:
reload(utils)
cov = utils.get_coverage('SRR650219.sorted.bam','RD900MAF',200,230)
print (cov)
p = plotters.plot_coverage(cov)
pn.pane.Bokeh(p)

In [187]:
#reference = 'Mbovis-AF212297.2.gb'
#filename = 'wt_mbovis.bam'
#chrom = 'NC_002945.4'
#gff = 'Mbovis_AF212297.gff'

filename = 'SRR650219.sorted.bam'
chrom = 'RD900MAF'
gff = 'RD900MAF.gff'

In [188]:
def get_chrom(bam_file):
    """Get first sequence name in a bam file"""
    
    import pysam
    samfile = pysam.AlignmentFile(filename, "r")
    iter=samfile.fetch(start=0,end=10)
    for read in iter:
        if read.reference_name:
            return read.reference_name

get_chrom(filename)

'RD900MAF'

In [269]:
def plot_empty():
    p = figure(plot_width=900,plot_height=80,tools="")
    p.grid.visible = False
    return p

def plot_bam_alignment(bam_file, chr, start, end, height=50, fontsize="12pt", plot_width=800, plot_height=250):
    """Bokeh bam alignments plotter.
    Args:
        bam_file: name of a sorted bam file
        start: start of range to show
        end: end of range        
    """
    
    if bam_file is None:
        return plot_empty()
    
    h=.2+height/plot_height    
    df = utils.get_bam_aln(bam_file, chr, start-200, end+200)
    if df is None:
        p = figure(title=None,plot_width=plot_width, plot_height=plot_height,tools="")
        #text = Label(x=.5, y=1, text='here your text')
        #p.add_layout(text)
        return p
    #offset for rects
    df['x'] = df.start+df.length/2
    #set colors by quality
    df['color'] = df.apply(lambda x: 'red' if x.mapq==0 else 'gray' ,1)
    df['span'] = df.apply(lambda x: str(x.start)+':'+str(x.end),1)
    
    source = ColumnDataSource(df)
    x_range=(start, end)
    hover = HoverTool(
        tooltips=[            
            ("name", "@name"),
            ("cigar", "@cigar"),
            ("span", "@span"),
            ("length", "@length"),
            ("mapq", "@mapq"),            
        ]
    )
    tools=[hover,"save"]
    
    p = figure(title=None, plot_width=plot_width, plot_height=plot_height, x_range=x_range, y_range=(0,height), tools=tools, 
                    min_border=0, toolbar_location='right')
    rects = Rect(x="x", y="y", width="length", height=h, fill_color="color", line_color='gray',fill_alpha=0.4)
    p.grid.visible = False
    p.add_glyph(source, rects)
    p.yaxis.visible = False
    p.xaxis.formatter = NumeralTickFormatter(format="(0,0)")
    p.toolbar.logo = None
    return p

In [127]:
reload(utils)
out = pn.pane.Bokeh()

feats = utils.genbank_to_features('Mbovis-AF212297.2.gb')
out.object = plotters.plot_features(feats,preview=False, plot_width=900,plot_height=80)
out

Bokeh(Figure)

In [212]:
def plot_sequence(seq, plot_width=1000, plot_height=20, fontsize='10pt', xaxis=False):
    """Plot a single sequence"""
    
    text = list(seq)    
    N = len(seq)
    x = list(range(N))
    
    colors = utils.get_sequence_colors([seq])    
    source = ColumnDataSource(dict(x=x, text=text, colors=colors))  
    x_range = Range1d(0,N+1, bounds='auto') 
    p = figure(plot_width=plot_width, plot_height=plot_height, x_range=x_range, y_range=(0,1), 
               tools="", min_border=0)    
    rects = Rect(x="x", y=0,  width=1, height=2, fill_color="colors", line_color=None, fill_alpha=0.4)
    p.add_glyph(source, rects)
    if len(seq)<200:
        glyph = Text(x="x", y=0, text="text", text_align='center',text_color="black", 
                     text_font="monospace",text_font_size=fontsize)    
        p.add_glyph(source, glyph)
    p.grid.visible = False
    if xaxis == False:
        p.xaxis.visible = False
    p.yaxis.visible = False
    p.toolbar.logo = None
    return p

out = pn.pane.Bokeh()
from pyfaidx import Fasta
refseq = Fasta('Mbovis-AF212297.fa')
key = list(refseq.keys())[0]
seq = refseq[key][1400:1708].seq

out.object = plot_sequence(seq)
#out.object = plot_empty()
out

Bokeh(Figure)

In [273]:
reload(viewers)
reload(utils)
reload(plotters)

bam_input = pnw.FileInput(name='bam file')
ref_input = pnw.FileInput(name='reference')
gff_input = pnw.FileInput(name='gff file')
colorby = pnw.Select(name='Color by', options=['quality','pair orientation','read strand'], width=180)
slider = pnw.IntSlider(name='location',start=10,end=10000,value=0,step=500,width=300)
main_pane = pn.pane.Bokeh(height=100)
cov_pane = pn.pane.Bokeh(height=60)
loc_pane = pn.pane.Str(50,width=180,style={'margin': '4pt'})
feat_pane = pn.pane.Bokeh(height=60)
ref_pane = pn.pane.Bokeh(height=60)
xzoom_slider = pnw.IntSlider(name='x zoom',start=50,end=2000,value=1000,step=10,width=100)
yzoom_slider = pnw.IntSlider(name='y zoom',start=10,end=200,value=50,step=5,width=100)#,orientation='vertical')
panleft_btn = pnw.Button(name='<',width=50,button_type='primary')
panright_btn = pnw.Button(name='>',width=50,button_type='primary')

height=200
width=1000

def pan_right(event):
    loc = slider.value+200    
    slider.value=loc
    refresh(event)
    return

def pan_left(event):
    loc = slider.value-200
    if loc<1:
        return
    slider.value=loc
    refresh(event)
    return

def update_features(event):
    """Load features"""
    
    filename = gff_input.filename
    ext = os.path.splitext(filename)[0]
    if ext == '.gff':
        feats = utils.gff_to_features(gff_input.filename)
    elif ext in ['.gb','.gbff']:
        feats = utils.genbank_to_features(gff_input.filename)
    feat_pane.object = plotters.plot_features(feats,preview=False, plot_width=width,plot_height=75)
    return

def update_ref(start, end):
    """Update reference sequence"""
    
    from pyfaidx import Fasta
    refseq = Fasta('Mbovis-AF212297.fa')
    key = list(refseq.keys())[0]
    seq = refseq[key][int(start):int(end)].seq
    ref_pane.object = plot_sequence(seq, plot_height=18,fontsize='10pt')
    return
    
def refresh(event):
    """Update viewers on widget change"""
    
    filename = bam_input.filename
    xzoom = xzoom_slider.value
    yzoom = yzoom_slider.value
    start = slider.value     
    N = xzoom/2
    end = start+N
    chrom = utils.get_chrom(bam_input.filename)
    loc_pane.object = '%s:%s-%s' %(chrom,start,end)
    if filename is None:        
        return
    cov = utils.get_coverage(filename,chrom,start,end)
    cov_pane.object = plotters.plot_coverage(cov,plot_width=width)
    main_pane.object = plot_bam_alignment(filename,chrom,start,end,height=yzoom,plot_width=width,plot_height=height)
    update_ref(start, end)
    return

slider.param.watch(refresh, 'value')
xzoom_slider.param.watch(refresh, 'value')
yzoom_slider.param.watch(refresh, 'value')
panright_btn.param.watch(pan_right, 'clicks')
panleft_btn.param.watch(pan_left, 'clicks')
bam_input.param.watch(refresh, 'value')
ref_input.param.watch(update_ref, 'value')
gff_input.param.watch(update_features, 'value')

#initialise slider
slider.param.trigger('value')

menus = pn.Row(bam_input, ref_input, gff_input)
top = pn.Row(slider,xzoom_slider,yzoom_slider,panleft_btn,panright_btn,loc_pane)
bottom = pn.Row(colorby)
main = pn.Column(menus,top,cov_pane,main_pane,ref_pane,feat_pane,bottom)
main

Column
    [0] Row
        [0] FileInput(name='bam file')
        [1] FileInput(name='reference')
        [2] FileInput(name='gff file')
    [1] Row
        [0] IntSlider(end=10000, name='location', start=10, step=500, width=300)
        [1] IntSlider(end=2000, name='x zoom', start=50, step=10, value=1000, width=100)
        [2] IntSlider(end=200, name='y zoom', start=10, step=5, value=50, width=100)
        [3] Button(button_type='primary', name='<', width=50)
        [4] Button(button_type='primary', name='>', width=50)
        [5] Str(str, style={'margin': '4pt'}, width=180)
    [2] Bokeh(Empty, height=60)
    [3] Bokeh(Empty, height=100)
    [4] Bokeh(Empty, height=60)
    [5] Bokeh(Empty, height=60)
    [6] Row
        [0] Select(name='Color by', options=['quality', 'pair orientat...], value='quality', width=180)

In [ ]:
reload(utils)
template = utils.get_template()
tmpl = pn.Template(template)
tmpl.add_panel('A',main)
tmpl